# MIR Project phase 2
## English Text classification using naive bayes

<div dir="rtl">این کد تماما مشابه فاز قبل است با این تفاوت که بخش ذخیره سازی را ندارد و به جای آن یک دسته بند برای دسته بندی داده ها اضافه شده است.
<br>
از بین دسته بند های بخش اول فاز دوم دسته بند naive bayes بیشترین درصد  accuracy را داشت به همین خاطر از این دسته بند در این بخش استفاده میکنیم.
</div>

In [1]:
import nltk
from nltk.corpus import stopwords
from nltk.stem import SnowballStemmer
from nltk import WordNetLemmatizer
from collections import Counter
import csv
import os
import math
import pickle
import numpy as np
from bitarray import bitarray

## first part
<div dir="rtl">حال به طراحی تابع prepare_text میپردازیم:</div>
<div dir="rtl">ابتدا با استفاده از کتابخانه ی csv فایل مورد نظر را خوانده ایم و و هر سطر را به دو قسمت title و description تقسیم کرده ایم.</div>
<div dir="rtl">آدرس فایل مورد نظر به عنوان آرگومان به تابع prepare text داده شده است.</div>
<div dir="rtl">سپس همه ی title و description ها را به صورت lowercase درآورده ایم و هر کدام را جداگانه در آرایه های temporary1 و temporary2 ریخته ایم.</div>
<div dir="rtl">حال آرگومان های دیگری نیز به تابع داده ایم که هر کدام از آن ها یک flag هستند و مشخص می کنند که آیا کار پیش رو انجام شود یا خیر. برای مثال delete_punctuation به عنوان یک flag می باشد و اگر کاربر آن را T بگذارد نشان دهنده ی این موضوع است که او میخواهد علائم نگارشی حذف شود و در صورتی که F بگذارد نمیخواهد آن ها را حذف کند. (در این بخش ما هرچه غیر از کلمات و حروف را حذف کرده ایم.)</div>
<div dir="rtl">حال با توجه به این موضوع اگر این flag برابر با T شود آنگاه علائم نگارشی حذف خواهند شد.</div>
<div dir="rtl">در مرحله ی بعدی flag ای وجود دارد که مشخص میکند آیا stopword ها حذف شوند یا خیر. برای این کار در ابتدای تابع متغیری با نام documents قرار داده ایم تا تمام مستندات در آن قرار گیرد. سپس با پردازش کل آن دریافتیم که حدود ۳۷ عدد از کلمات پر تکرار را به عنوان ایست واژه در نظر بگیریم و سپس در هر کدام از description ها و title ها در صورت وجود آن کلمات آن ها را حذف خواهیم کرد.</div>
<div dir="rtl">یک flag دیگر نیز برای stemming خواهیم داشت و در صورتی که کاربر آن را T بگذارد stemming انجام خواهد شد. برای اینکار از SnowballStemmer استفاده کرده ایم.</div>
<div dir="rtl">حال که پیش پردازش تمام شده است تمام token هایی که درون temporary ذخیره کرده بودیم را درون آرایه ی tokens میریزیم تا همه ی token ها در همه ی مستندات را داشته باشیم.</div>
<div dir="rtl"> در نهایت تمام توکن های موجود در آرایه های temporary را در درون آرایه های description و title میریزیم.</div>
<div dir="rtl">پس از آن از counter استفاده کرده ایم تا لغات را بشمارد و به ترتیب نزولی نمایش دهد.</div>
<div dir="rtl">سپس مقادیر موجود در آن counter را به عنوان لیست tf یا term frequency ذخیره کرده ایم چون به آن در مراحل بعدی نیاز پیدا خواهیم کرد.</div>

In [2]:
def prepare_text(address, delete_punctuation, delete_stopWords, stemming):
        description = []
        title = []
        documents = ""
        totalDocs = []
        with open(address, newline='') as csvfile:
            reader = csv.DictReader(csvfile)
            for row in reader:
                description += [row['description']]
                title += [row['title']]
                documents += row['description']+" "+row['title']
                totalDocs += [row['description']+" "+row['title']]

        tokens=nltk.word_tokenize(documents)
        word = Counter(tokens)
        stopwords = word.most_common(37)

        tokens = []
        for i in range(len(description)):
            temporary1 = []
            description[i] = description[i].lower()
            temporary1 += nltk.word_tokenize(description[i])
            
            temporary2 = []
            title[i] = title[i].lower()
            temporary2 += nltk.word_tokenize(title[i])

            #### deleting punctuations
            if delete_punctuation=="T":
                temporary1 = [i
                for i in temporary1
                    if i.isalpha()]
                
            if delete_punctuation=="T":
                temporary2 = [i
                for i in temporary2
                    if i.isalpha()]

            ### finding and deleting stopwords
            if delete_stopWords=="T":
                temporary1 = [i
                for i in temporary1
                    if i not in stopwords]
                
            if delete_stopWords=="T":
                temporary2 = [i
                for i in temporary2
                    if i not in stopwords]

            #### stemming
            if stemming=="T":
                stemmer = SnowballStemmer("english")
                temporary1 = [stemmer.stem(i)
                for i in temporary1]
            if stemming=="T":
                stemmer = SnowballStemmer("english")
                temporary2 = [stemmer.stem(i)
                for i in temporary2]
            
            tokens += temporary1
            tokens += temporary2

            #changing the document to processed one
            description[i] = temporary1
            title[i] = temporary2

        #### number of tokens
        word = Counter(tokens)
        tf = word.most_common()
#         print("The terms after preprocessing are:")
#         print(tokens)
#         print("the number of each term is:")
#         print(tf)
        return description , title,tokens,stopwords,totalDocs

## second part
<div dir="rtl">حال به بخش دوم می پردازیم:</div>
<div dir="rtl">در این بخش از pickle استفاده کرده ایم.</div>
<div dir="rtl">در این بخش به ساختن positional index میپردازیم:</div>
<div dir="rtl">در این بخش به این صورت عمل کرده ایم که ابتدا ترم مربوط می آید و سپس شماره ی مستند و سپس zone مربوط به آن مستند که در title آن داکیومنت وجود داشته است یا در قسمت description آن و در نهایت جایگاه آن نشان داده خواهد شد. </div>

In [3]:
def positional_index_dictionary_maker(title , description, deleted_doc):
    positional_index = {}
    for i in range(len(description)):
        if deleted_doc[i] ==False:
            index_counter = 0
            for word in title[i]:
                if word in positional_index:
                    newTermInDoc = True
                    for doc_elm in positional_index[word]:
                        if i == doc_elm[0]:
                            doc_elm[1].get('title').append(index_counter)
                            newTermInDoc = False
                            break
                    if newTermInDoc == True:
                        positional_index[word].append((i,{'title': [index_counter]}))
                else: positional_index[word] = [(i,{'title': [index_counter]})]
                index_counter += 1
            index_counter = 0
            for word in description[i]:
                if word in positional_index:
                    newTermInDoc = True
                    for doc_elm in positional_index[word]:
                        if i == doc_elm[0]:
                            if('description' in doc_elm[1].keys()):
                                doc_elm[1]['description'].append(index_counter)
                            else:
                                doc_elm[1]['description'] = []
                                doc_elm[1]['description'].append(index_counter)
                            newTermInDoc = False
                            break
                    #if word is in dict but the doc isnt
                    if newTermInDoc == True:
                        positional_index[word].append((i,{'description': [index_counter]}))
                #if there is word hsa not been saved in dict
                else: positional_index[word] = [(i,{'description': [index_counter]})]
                index_counter += 1
    return positional_index

<div dir="rtl">حال برای اضافه کردن یک مستند به مجموع مستندات ابتدا آدرس آن را میگیریم و پیش پردازش های لازم را روی آن انجام میدهیم و سپس آن را به نمایه های قبلی اضافه میکنیم. </div>

In [4]:
def positional_add_document(address, delete_punctuations, delete_stopWords, stemming,
                           title,description, deleted_doc,
                                               positions):

    newdescription , newtitle,t,s,t1=prepare_text(address, delete_punctuations,
                                           delete_stopWords, stemming)
    description += [newdescription]
    title += [newtitle]
    deleted_doc+=[False]
    count = 0
    flag = False
    for token in newtitle:
        flag = False
        if token in positions:
            for j in range(len(positions[token])):
                if positions[token][j][0] == len(title)-1:
                    if "title" in positions[token][j][1]:
                        positions[token][j][1]["title"].append(count)
                    else:
                        positions[token][j][1]["title"]=[count]
                    flag =True
                    break
            if flag==False:   
                positions[token] += [(len(title)-1 , {"title":[count]})]
        else:
            positions[token] = [(len(title)-1 , {"title":[count]})]
        count += 1

    count = 0
    flag = False
    for token in newdescription:
        flag = False
        if token in positions:
            for j in range(len(positions[token])):
                if positions[token][j][0] == len(description)-1:
                    if "description" in positions[token][j][1]:
                        positions[token][j][1]["description"].append(count)
                    else:
                        positions[token][j][1]["description"]=[count]
                    flag =True
                    break
            if flag==False:   
                positions[token] += [(len(description)-1 , {"description":[count]})]
        else:
            positions[token] = [(len(description)-1 , {"description":[count]})]
        count += 1
    return positions

<div dir="rtl">حال برای حذف کردن یک مستند از مجموعه مستندات کافی است که خانه ی docID مربوط به آن مستند true شود و در درون positional index در صورتی نمایه سازی انجام خواهد شد که خانه ی مربوطه false باشد.</div>

In [5]:
def delete_document(docID , deleted_doc):
    deleted_doc[docID]=True
    return deleted_doc

<div dir="rtl">حال به محاسبه ی bigram میپردازیم و در صورتی که داکیومنتی حذف نشده بود کلمات آن به شکل bigram ذخیره میشوند.</div>

In [6]:
def bigram_dictionary_maker(docs,deleted_doc):
    resault = {}
    count =0
    for doc in docs:
        if deleted_doc[count]==False:
            for term in doc:
                chars = ['$']
                for i in range(len(term)):
                    chars.append(term[i])
                chars.append('$')
                for i in range(len(chars) - 1):
                    current = chars[i] + chars[i + 1]

                    if current in resault:
                        newTermInDoc = True
                        for doc_elm in resault[current]:
                            if term == doc_elm:
                                newTermInDoc = False
                                break
                        if newTermInDoc == True:
                            resault[current].append(term)
                    else: resault[current] = [term]
        count+=1                  
    return resault

<div dir="rtl">حال در صورت اضافه کردن مستندی به مجموعه مستندات term های مستند جدید را به bigram تبدیل کرده و به bigram های پیشین اضافه میکنیم.</div>

In [7]:
def bigram_add_document(current_bigram, address,description,title,
                        delete_punctuations,delete_stopWords,
                        stemming,documents,deleted_Docs):

    newdes , newtit,t,s,t1=prepare_text(address, delete_punctuations, delete_stopWords, stemming)
    description += [newdescription]
    title += [newtitle]
    deleted_doc+=[False]
    current_bigram = {}
    for term in doc:
        chars = ['$']
        for i in range(len(term)):
            chars.append(term[i])
        chars.append('$')
        for i in range(len(chars) - 1):
            current = chars[i] + chars[i + 1]

            if current in current_bigram:
                newTermInDoc = True
                for doc_elm in current_bigram[current]:
                    if term == doc_elm:
                        newTermInDoc = False
                        break
                if newTermInDoc == True:
                    current_bigram[current].append(term)
            else: current_bigram[current] = [term]
                      
    return current_bigram

## fourth part
<div dir="rtl">حال به بخش چهارم می پردازیم:</div>
<div dir="rtl">ابتدا تابعی برای معیار جاکارد زده ایم. به این صورت که اشتراک دو لیست از بایگرام ها را به روی اجتماع آن ها محاسبه می کند.</div>

In [8]:
def jaccard(list1, list2):
    intersection = len((set(list1).intersection(list2)))
    union = (len(list1) + len(list2)) - intersection
    return float(intersection / union)

<div dir="rtl">در نهایت با استفاده از معیار جاکارد و بایگرام ها لیستی از امتیازات sort شده به صورت نزولی را در می آوریم.</div>

In [9]:
def find_relevance_of_words(query, all_words,deleted_doc):
    resault = {}
    q = list(bigram_dictionary_maker([[query]],[False]).keys())
    for word in all_words:
        resault[word] = jaccard(q, list(bigram_dictionary_maker([[word]],deleted_doc).keys()))
        
    return dict(sorted(resault.items(), key=lambda x: x[1], reverse=True))

<div dir="rtl">در نهایت با استفاده از الگوریتم edit distance بهترین کلمه ای را که میتواند جایگزین کلمه ی اشتباه موجود در query باشد را از میان کلمات انتخاب شده از معیار جاکارد انتخاب می کنیم و به عنوان خروجی می دهیم:</div>

In [10]:
def edit_distance(words, query_word):
    distance = []
    for word in words:
        matrix = [[0 for i in range(len(word)+1)] for j in range(len(query_word)+1)]
        for i in range(len(word)+1):
            matrix[0][i] = i
        for i in range(len(query_word)+1):
            matrix[i][0] = i
        for i in range(1,len(query_word)+1):
            for j in range(1,len(word)+1):
                scores = []
                scores += [matrix[i-1][j] +1]
                scores += [matrix[i][j-1] +1]
                if word[j-1]==query_word[i-1]:
                    scores+= [matrix[i-1][j-1]]
                else:
                    scores += [matrix[i-1][j-1]+1]
                matrix[i][j] = min(scores)
        distance += [matrix[len(query_word)][len(word)]]
    choosen_word = words[distance.index(min(distance))]
    return choosen_word

<div dir="rtl">حال باید در صورت ورود کوئری آن را مانند مستندات پیش پردازش کنیم:</div>

In [11]:
def prepare_query(query,stopwords,delete_punctuation, delete_stopWords, stemming):

        token = []
        query = query.lower()
        token += nltk.word_tokenize(query)

        #### deleting punctuations
        if delete_punctuation=="T":
            token = [i
            for i in token
                if i.isalpha()]

        ### finding and deleting stopwords
        if delete_stopWords=="T":
            token = [i
            for i in token
                if i not in stopwords]

        #### stemming
        if stemming=="T":
            stemmer = SnowballStemmer("english")
            token = [stemmer.stem(i)
            for i in token]

        return token

## fifth part
<div dir="rtl">در این قسمت idf را پیاده سازی میکنیم:</div>

In [12]:
def idf_calculator(positional_index, term, n):
    posting = positional_index.get(term)
    if(posting != None):
        df = len(posting)
        idf = math.log(n/df)
    else:
        return 0
    return idf

<div dir="rtl">حال باید از کد زیر استفاده کنیم تا بتوانیم normalization انجام دهیم:</div>

In [13]:
def cosine_normalizing_factor(positional_index, N):
    M = len(positional_index.items())
    text_vector = [0 for i in range(N)]
    title_vector = [0 for i in range(N)]
    for key, value in positional_index.items():
        for doc in value:
            if 'text' in doc[1].keys():
                tf = 1 + math.log(len(doc[1].get('text')))
            else: tf = 0
            text_vector[doc[0]] += tf**2
            if 'title' in doc[1].keys():
                tf = 1 + math.log(len(doc[1].get('title')))
            else: tf = 0
            title_vector[doc[0]] += tf**2
    text_vector = [math.sqrt(v) for v in text_vector]
    title_vector = [math.sqrt(v) for v in title_vector]
    return text_vector, title_vector

<div dir="rtl">در این قسمت از معیار tf-idf استفاده کرده ایم تا ۱۰ مستند مرتبط را برگردانیم:</div>

In [14]:
def tfidfweighter(query, positional_index, n):
    text, title = cosine_normalizing_factor(positional_index, n)
    vectors = {}
    #finding documents with their scores for the words of query
    for i in range(len(query)):
        posting = positional_index.get(query[i])
        if(posting != None):
            for doc in posting:
                if 'title' in doc[1].keys():
                    title_tf = 1 + math.log(len(doc[1].get('title')))
                else: title_tf = 0
                if 'text' in doc[1].keys():
                    text_tf = 1 + math.log(len(doc[1].get('text')))
                else: text_tf = 0
                if doc[0] not in vectors.keys():
                    vectors[doc[0]] = [0 for i in range(len(query))]
                if(title[doc[0]] == 0 ):
                    vectors[doc[0]][i] = text_tf/text[doc[0]]
                elif (text[doc[0]] == 0) :
                    vectors[doc[0]][i] = title_tf/title[doc[0]]
                else:
                    vectors[doc[0]][i] = text_tf/text[doc[0]] + title_tf/title[doc[0]]  
    #calculating the weights of query
    weights = [0 for i in range(len(query))]
    for i in range(len(query)):
        tf = 1 + math.log(query.count(query[i]))
        idf = idf_calculator(positional_index, query[i], n)
        weights[i] = tf * idf
    normalizer = np.linalg.norm(weights)
    weights = [w/normalizer for w in weights]
    ranks = []
    for docid, value in vectors.items():
        pr = np.dot(weights, value)
        ranks.append((pr, docid))
    ranks = sorted(ranks, reverse=True)
    return ranks[:50]

## classifing documents using naive bayes

In [15]:
class naive_bayes_classifier:
    def __init__(self, address, delete_punctuation, delete_stopWords, stemming):
        self.documents, self.tokens = self.prepare_text(address, delete_punctuation, delete_stopWords, stemming)
        self.logPriors = self.logpriorclass(self.documents)
        self.lessTokens, self.moreTokens = self.class_freq_dict(self.documents)
        
    def prepare_text(self, address, delete_punctuation, delete_stopWords, stemming):
        documents = []
        totalDocs = ""
        with open(address, newline='') as csvfile:
            reader = csv.DictReader(csvfile)
            for row in reader:
                doc = {}
                doc['title'] = row['title']
                doc['description'] = row['description']
                doc['views'] = row['views']
                totalDocs += row['description'].lower()+" "+row['title'].lower()
                documents.append(doc)

        totalDocs = nltk.word_tokenize(totalDocs)
        totalDocs = [i for i in totalDocs
                        if i.isalpha()]
        word = Counter(totalDocs)
        stopwords = [i[0] for i in word.most_common(37)]
        #print(stopwords)
        
        tokens = {}
        for i in range(len(documents)):
            doc = documents[i]
            title = doc.get('title').lower()
            title = nltk.word_tokenize(title)
            desc = doc.get('description').lower()
            desc = nltk.word_tokenize(desc)

            #### deleting punctuations
            if delete_punctuation=="T":
                title = [i
                for i in title
                    if i.isalpha()]
                desc = [i
                for i in desc
                    if i.isalpha()]

            ### finding and deleting stopwords
            if delete_stopWords=="T":
                title = [i
                for i in title
                    if i not in stopwords]
                if 'the' in title:
                    print('1')
                desc = [i
                for i in desc
                    if i not in stopwords]
            
            #### stemming
            if stemming=="T":
                stemmer = SnowballStemmer("english")
                title = [stemmer.stem(i)
                for i in title]
                desc = [stemmer.stem(i)
                for i in desc]
            
            #calculating the df of each word
            temp = set()
            for word in title:
                    temp.add(word)
            for word in desc:
                    temp.add(word)
            for word in temp:
                if word in tokens.keys():
                    tokens[word][0] += 1
                else:
                    tokens[word] = [1, len(tokens)]
            #changing the document to processed one
            documents[i]['title'] = title
            documents[i]['description'] = desc
       
        
        return documents, tokens
    
    def logpriorclass(self, documents):
        n = len(documents)
        lessviews = 0
        moreviews = 0
        for i in range(n):
            if documents[i].get('views') == '-1':
                lessviews += 1
            else:
                moreviews += 1
        return math.log(lessviews/n), math.log(moreviews/n)

    def class_freq_dict(self,documents):
        lesstokens = {}
        moretokens = {}
        for i in range(len(documents)):
            text = []
            text = documents[i].get('title') + documents[i].get('description')
            if documents[i].get('views') == '-1':
                temp = set(text)
    #             print(temp)
                for word in temp:
                    #print(word, text.count(word))
                    if word in lesstokens.keys():
                        lesstokens[word] += text.count(word)
                    else:
                        lesstokens[word] = text.count(word)
            else:
                temp = set(text)
                for word in temp:
                    #print(word, text.count(word))
                    if word in moretokens.keys():
                        moretokens[word] += text.count(word)
                    else:
                        moretokens[word] = text.count(word)
        return lesstokens, moretokens

    def predicter(self, doc, trainTokens, moreTokens, lessTokens, logpriors):
        text = []
        text = doc.get('title') + doc.get('description')
        more_score = 0
        less_score = 0
        more_num, less_num = sum(moreTokens.values()), sum(lessTokens.values())
        for word in text:
            if word not in trainTokens:
                continue
            #calculating the score of less class
            log_likelihood_less = math.log( (1 + lessTokens.get(word, 0.0))/(less_num + len(trainTokens)))
            less_score += log_likelihood_less 
            #calculating the score of less class
            log_likelihood_more = math.log( (1 + moreTokens.get(word, 0.0)) / (more_num + len(trainTokens)))
            more_score += log_likelihood_more 

        log_prior_more = logpriors[1]
        more_score += log_prior_more
        log_prior_less = logpriors[0]
        less_score += log_prior_less
    #     print(more_score, less_score)
        if more_score > less_score:
            return 1
        else:
            return -1
    
    def predict(self, doc):
        return self.predicter(doc, self.tokens, self.moreTokens, self.lessTokens, self.logPriors)

In [16]:
classifier = naive_bayes_classifier("data/train.csv", "T", "T", "T")

In [17]:
add = "data/ted_talks.csv"
print("please enter what you want. if you want something type T else type F:")
print("deleting punctuations:")
delete_punctuations = input()
print("deleting stopwords:")
delete_stopWords = input()
print("stemming:")
stemming = input()
description ,title,tokens,stopwords,totalDocs= prepare_text(add, delete_punctuations, delete_stopWords, stemming)
labels = []
for i in range(len(description)):
    doc = {}
    doc['title'] = title[i]
    doc['description'] = description[i]
    views = classifier.predict(doc)
    labels.append(views)
#print(labels)

please enter what you want. if you want something type T else type F:
deleting punctuations:
T
deleting stopwords:
T
stemming:
T


# UI

<div dir="rtl">حال با کاربر ارتباط برقرار می کنیم:</div>
<div dir="rtl">در این بخش ابتدا می بینیم که آیا کاربر میخواهد علائم نگارشی را حذف کند یا آیا می خواهد ایست واژه ها را حذف کند یا آیا میخواهد stemming انجام شود یا خیر.</div>
<div dir="rtl">سپس پیش پردازش بر روی مستندات انجام میشود:</div>

In [18]:
add = "data/ted_talks.csv"
print("please enter what you want. if you want something type T else type F:")
print("deleting punctuations:")
delete_punctuations = input()
print("deleting stopwords:")
delete_stopWords = input()
print("stemming:")
stemming = input()
description , title,tokens,stopwords,totalDocs= prepare_text(add, delete_punctuations, delete_stopWords, stemming)
classifier = naive_bayes_classifier("data/train.csv", delete_punctuations, delete_stopWords, stemming)
labels = []
for i in range(len(description)):
    doc = {}
    doc['title'] = title[i]
    doc['description'] = description[i]
    views = classifier.predict(doc)
    labels.append(views)

please enter what you want. if you want something type T else type F:
deleting punctuations:
T
deleting stopwords:
T
stemming:
T


<div dir="rtl">در این بخش در خط اول آرایه ای به اندازه ی طول مستندات ذخیره کرده ایم تا بعدا بتوانیم از آن در قسمت حذف مستندات استفاده کنیم.</div>
<div dir="rtl">در خط دوم جایگاه ها را به روش positional index ذخیره کرده ایم تا بعدا از آن استفاده کنیم.</div>
<div dir="rtl">سپس به روش بایگرام بایگرام ها را ذخیره کرده ایم و در انتها در دو فایل این ایندکس ها را ذخیره کرده ایم.</div>

In [19]:
deleted_doc = [False]*(len(title))
positions = positional_index_dictionary_maker(title,description , deleted_doc)
documents = []
for i in range(len(description)):
    documents += [title[i]+description[i]]
bigrams = bigram_dictionary_maker(documents,deleted_doc)

<div dir="rtl">حال تمام positional index ها به شکل زیر است:</div>

In [20]:
print("The total positional posting list is:")
print(positions)

The total positional posting list is:
{'do': [(0, {'title': [0]}), (5, {'title': [2, 5]}), (9, {'description': [41]}), (43, {'description': [1]}), (47, {'description': [1]}), (72, {'description': [29]}), (83, {'description': [26]}), (88, {'description': [10]}), (94, {'description': [5]}), (109, {'description': [1]}), (110, {'title': [4]}), (131, {'description': [57]}), (136, {'description': [21]}), (168, {'description': [29]}), (171, {'title': [7], 'description': [19]}), (174, {'description': [18]}), (183, {'description': [13, 22]}), (208, {'description': [30, 35]}), (226, {'description': [10]}), (233, {'description': [30]}), (247, {'description': [10]}), (257, {'description': [14]}), (259, {'description': [1]}), (278, {'description': [16]}), (281, {'description': [16, 23]}), (284, {'description': [26]}), (286, {'description': [28, 36]}), (316, {'description': [23]}), (319, {'title': [1], 'description': [1]}), (323, {'description': [32]}), (328, {'description': [16]}), (344, {'title': 

<div dir="rtl">در این قسمت کاربر میتواند کلمه ی مورد نظر خود را وارد کند تا posting list و جایگاه آن را در هر مستند ببیند.</div>

In [21]:
print("please enter a word that you want to know its positional posting list:")
term = input()
stemmer = SnowballStemmer("english")
term = stemmer.stem(term)
for word in positions:
    if word == term:
        print(positions[word])

please enter a word that you want to know its positional posting list:
school
[(0, {'title': [1]}), (8, {'title': [6], 'description': [12]}), (131, {'description': [41]}), (171, {'description': [9]}), (203, {'title': [5], 'description': [18]}), (293, {'title': [3], 'description': [21]}), (361, {'description': [16]}), (387, {'description': [9]}), (480, {'description': [17]}), (529, {'description': [14]}), (592, {'description': [8]}), (692, {'description': [20]}), (694, {'title': [2]}), (711, {'description': [2]}), (715, {'description': [41, 47]}), (760, {'description': [16]}), (767, {'description': [4]}), (815, {'title': [2], 'description': [9, 11, 35]}), (833, {'description': [18]}), (848, {'description': [12]}), (866, {'description': [38]}), (882, {'title': [6], 'description': [1]}), (911, {'description': [2]}), (947, {'description': [24]}), (960, {'description': [42]}), (1023, {'title': [6], 'description': [18, 23]}), (1038, {'description': [5]}), (1216, {'description': [19]}), (1233

<div dir="rtl">در این قسمت کاربر میتواند با وارد کردن یک کلمه شماره ی مستندات مربوط و یا به عبارتی posting list آن را ببیند:</div>

In [22]:
print("please enter a word that you want to know its posting list:")
term = input()
stemmer = SnowballStemmer("english")
term = stemmer.stem(term)
documentIDs = []
for word in positions:
    if word == term:
        for j in range(len(positions[word])):
            documentIDs += [positions[word][j][0]]
print(documentIDs)

please enter a word that you want to know its posting list:
school
[0, 8, 131, 171, 203, 293, 361, 387, 480, 529, 592, 692, 694, 711, 715, 760, 767, 815, 833, 848, 866, 882, 911, 947, 960, 1023, 1038, 1216, 1233, 1276, 1294, 1352, 1410, 1420, 1429, 1433, 1441, 1445, 1451, 1498, 1499, 1500, 1501, 1509, 1595, 1615, 1640, 1706, 1792, 1804, 1832, 1855, 1913, 1957, 1991, 1992, 2023, 2049, 2073, 2077, 2099, 2122, 2149, 2201, 2232, 2285, 2288, 2316, 2346, 2355, 2374, 2377, 2445, 2454, 2466, 2482, 2522, 2545, 2547]


<div dir="rtl">در این قسمت کاربر با وارد کردن یک کلمه و شماره ی مستند می تواند جایگاه های آن کلمه در آن مستند را ببیند:</div>

In [23]:
print("Please enter a word and documentID that you want to know its position:")
term=input()
stemmer = SnowballStemmer("english")
term = stemmer.stem(term)
docID = int(input())
for word in positions:
    if word == term:
        for j in range(len(positions[word])):
            if positions[word][j][0] == docID:
                print(positions[word][j][1])

Please enter a word and documentID that you want to know its position:
school
0
{'title': [1]}


<div dir="rtl">بایگرام ها به شکل زیر هستند:</div>

In [24]:
print("The total bigram indexing is:")
print(bigrams)

The total bigram indexing is:
{'$d': ['do', 'david', 'detail', 'data', 'drama', 'debunk', 'develop', 'discuss', 'door', 'day', 'design', 'dazzl', 'dizzi', 'dalla', 'dan', 'dennett', 'disput', 'deni', 'demonstr', 'describ', 'distribut', 'deliv', 'disast', 'dream', 'distant', 'deutsch', 'dawkin', 'deal', 'drug', 'dealer', 'don', 'dissatisfi', 'drive', 'de', 'diseas', 'democraci', 'did', 'document', 'devic', 'depress', 'donnelli', 'devast', 'demon', 'doe', 'discov', 'diet', 'dean', 'danish', 'davi', 'divers', 'disappear', 'dharamsala', 'dark', 'decept', 'danc', 'dancer', 'deaver', 'digit', 'differ', 'dna', 'discoveri', 'demand', 'depend', 'deep', 'diamond', 'display', 'determin', 'dolbi', 'deaf', 'done', 'down', 'delight', 'displac', 'director', 'duet', 'dedic', 'desert', 'demo', 'dreamscap', 'doerr', 'daughter', 'desktop', 'dollar', 'deepest', 'danger', 'deepli', 'digniti', 'depart', 'defens', 'dictionari', 'doom', 'declin', 'darfur', 'deborah', 'documentari', 'defi', 'delici', 'damag', 

<div dir="rtl">در این بخش کاربر می تواند بایگرام دلخواه خود را وارد کند و کلمات شامل آن بایگرام را ببیند:</div>

In [25]:
print("please enter a bigram to see the terms that contain it:")
bigram = input()
for bi in bigrams:
    if bi == bigram:
        print(bigrams[bi])

please enter a bigram to see the terms that contain it:
cd
['anecdot', 'mcdonough', 'mcdougal', 'mcdaniel', 'macdonald', 'xkcd', 'ocd']


<div dir="rtl">در این بخش کاربر میتواند آدرس مستندی را که میخواهد اضافه کند بدهد و در نتیجه جایگاه آن ها و بایگرام ها را بگیرد.</div>

In [ ]:
print("Please enter the address of a document that you want to add to other documents:")
address = input()
positions = positional_add_document(address, delete_punctuations, delete_stopWords,
                                    stemming,title,description, deleted_doc,positions)
bigrams = bigram_add_document(bigrams, address,description,title,
                        delete_punctuations,delete_stopWords,
                        stemming,documents,deleted_Docs)
print("The positions are:")
print(positions)
print("The bigrams are:")
print(bigrams)

<div dir="rtl">در این قسمت شماره ی مستندی را که میخواهیم حذف کنیم می دهیم و در نتیجه بایگرام و پوزیشنال ایندکس را میگیریم.</div>

In [ ]:
print("please enter the documentID that you want to delete it:")
documentID = int(input())
delete_doc = delete_document(documentID , deleted_doc)
bigrams = bigram_dictionary_maker(documents,deleted_doc)
positions = positional_index_dictionary_maker(title,description , deleted_doc)
print("The bigrams are:")
print(bigrams)
print("The positions are:")
print(positions)

<div dir="rtl">در این بخش کاربر باید چیزی را که میخواهد جستجو کند وارد کند. در صورت وجود غلط املایی آن را شناسایی و تصحیح میکنیم:</div>

In [36]:
print("Do you want to search in most viewed Talks?:(T/F)")
query_class = input()
if query_class == 'T':
    query_class = 1
else:
    query_class = -1
print("Please enter your query:")
query = input()
query_terms=prepare_query(query,stopwords,delete_punctuations, delete_stopWords, stemming)
true_word = []
for word in query_terms:
    if word not in tokens:
        wrong_word = word
        dic = find_relevance_of_words(word , tokens,deleted_doc)
        related_word =[]
        count = 0
        for i in dic:
            if count<=50:
                related_word += [i]

            else:
                break
            count+=1
        true_word += [edit_distance(related_word , wrong_word)]
    else:
        true_word += [word]
# print(true_word)
for i in range(len(true_word)):
    query =query.replace(query_terms[i],true_word[i])
print("Did you mean "+query+"?")

Do you want to search in most viewed Talks?:(T/F)
T
Please enter your query:
Do schols kill creativity?
Did you mean Do schools kill creativity??


<div dir="rtl">در این قسمت id ده مستند مربوط را چاپ می کنیم. سپس کاربر میتواند از میان آن ها هر کدام را که می خواهد انتخاب و مشاهده نماید:</div>

In [37]:
print("The best results of "+query+" are:")
tf_idf = tfidfweighter(true_word, positions, len(title))
for i in range(len(tf_idf)):
    if labels[tf_idf[i][1]] == query_class :
        print(tf_idf[i][1])
    else:
        continue
print("Please enter the documentID that you want to see:")
doc = int(input())
print(totalDocs[doc])

The best results of Do schools kill creativity? are:
0
1652
1376
1951
1483
1583
1100
1499
381
219
158
1451
293
332
2321
1525
1922
1445
203
1935
1233
1500
2454
882
2236
2115
1895
1810
8
2316
2003
5
2049
1991
Please enter the documentID that you want to see:
0
Sir Ken Robinson makes an entertaining and profoundly moving case for creating an education system that nurtures (rather than undermines) creativity. Do schools kill creativity?
